# Decrypt IBM

In [18]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob
from pathlib import Path
import requests
import json
from pprint import pprint
from multiprocessing.pool import ThreadPool
import threading
import urllib.request
import hashlib
import subprocess

from tqdm import tqdm_notebook as tqdm
import pandas as pd
import numpy as np
from random import randint

import sys
sys.path.append('/work/megapixels_dev/megapixels')
from app.utils import api_utils, identity_utils
from app.settings import app_cfg
from app.settings import types

In [20]:
fp_dir_research = '/data_store_hdd/datasets/people/ibm_dif/research/'
fp_usernames = join(fp_dir_research, 'username_sha.csv')
dir_json = '/data_store_hdd/datasets/people/ibm_dif/research/valid_files/'

## Decrypt

In [21]:
def decrypt(username, shaval):
  cmd = ['/home/adam/.nvm/versions/node/v9.9.0/bin/node', 
       '/data_store/datasets/people/ibm_dif/web_files/decrypt_cli', 
       username,
      shaval]
  proc = subprocess.Popen(cmd, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
  o, e = proc.communicate()
  return json.loads(o.decode())

In [ ]:
a = {'a':1, 'b':2}
c = {'c':3}


In [22]:
df_usernames = pd.read_csv(fp_usernames)

In [23]:
records = df_usernames.to_dict('records')

In [24]:
print(len(matched_records), len(records))

96414 581092


In [25]:
# create list of valid files
matched_records = []

for record in tqdm(records):
  shaval = record['sha256']
  username = record['username']
  fp_in = join(dir_json, shaval + '.json')
  if Path(fp_in).is_file():
      matched_records.append({'sha256':shaval, 'username': username})

In [26]:
print(len(matched_records))

48931


In [27]:
for record in tqdm(matched_records):
  if record['url'] and record['count']:
    continue
  shaval = record['sha256']
  username = record['username']
  fp_in = join(dir_json, shaval + '.json')
  if Path(fp_in).is_file():
    try:
      result = decrypt(username, shaval)
      obj = {'sha256':shaval, 'username': username, 'count': result['count'], 'url': result['url']}
      matched_records.append(obj)
    except Exception as e:
      print('Error:', e)

Error: Expecting value: line 1 column 1 (char 0)
Error: Expecting value: line 1 column 1 (char 0)
Error: Expecting value: line 1 column 1 (char 0)
Error: Expecting value: line 1 column 1 (char 0)
Error: Expecting value: line 1 column 1 (char 0)


KeyboardInterrupt: 

In [ ]:
df_records = pd.DataFrame.from_dict(matched_records)
df_records.to_csv('/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_metadata.csv', index=False)

In [ ]:
# make a CSV for downloading
filemaps = []
for item in matched_records:
  fp = join(Path(a).parent.name, Path(a).name)
  obj = {'filepath': fp, 'url': item['url']}
  filemaps.append(obj)
df_filemaps = pd.DataFrame.from_dict(filemaps)
df_filemaps.to_csv('/data_store_hdd/datasets/people/ibm_dif/research/ibm_dif_urls.csv', index=False)

In [ ]:
# working example
username = 'lknobel'
shaval = '00036fc3de043beca0c00a88d9d5cec4853a2d9a42c9c1ffdbb0e1f7431c488d'
result = decrypt(username, shaval)
print(result['count'])